In [2]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
import pandas as pd

In [3]:
# Read in data
df = pd.read_csv("../../data/raw/USGS_Water_Levels/usgs_water_levels.tsv", sep='\t', skiprows=29).tail(-1) # Skip to header, drop first row

# Rename columns, drop na
df = df.rename(columns={"178324_62614_00003": "water_elev_ft", "178324_62614_00003_cd": "data_integrity"}).dropna()

# Split datetime into separate columns
df[['year', 'month', 'day']] = df['datetime'].str.split("-", expand=True)

# Convert to numeric
df['year'] = pd.to_numeric(df['year'])
df['month'] = pd.to_numeric(df['month'])
df['day'] = pd.to_numeric(df['day'])
df['datetime'] = pd.to_datetime(df['datetime'])
df['water_elev_ft'] = pd.to_numeric(df['water_elev_ft'])

df.head()

agency_cd   site_no   datetime  water_elev_ft data_integrity  year  month  \
1       USGS  10010100 1966-04-15         4194.9              A  1966      4   
17      USGS  10010100 1966-05-01         4194.9              A  1966      5   
31      USGS  10010100 1966-05-15         4194.9              A  1966      5   
48      USGS  10010100 1966-06-01         4194.9              A  1966      6   
62      USGS  10010100 1966-06-15         4194.6              A  1966      6   

    day  
1    15  
17    1  
31   15  
48    1  
62   15

In [127]:
# Save number of years in which the lake's elevation was recorded
num_years = df['year'].nunique()
unique_years = df['year'].unique()

# Save colors
lake_col = "#265F58"
toxic_col = "#763A4F"
shrimp_col = "#556A82"

# Save elevation levels
brine_shrimp_elev = 4191
lake_bed_elev = 4196.3593632

# Create figure
fig = make_subplots(rows=2, cols=1, subplot_titles=['All Recorded Years', 'By Year'])

# Add plot with full time series
fig.append_trace(
    go.Scatter(
        visible=True,
        line=dict(color=lake_col, width=2),
        name="",
        x=df['datetime'],
        y=df['water_elev_ft']
    ),
    row=1,
    col=1
)

# Add lines to indicate dried lakebed level and healthy brine shrimp level
fig.append_trace(
    go.Scatter(
        visible=True,
        line=dict(color=toxic_col, width=2),
        name="",
        x=df['datetime'],
        y=[lake_bed_elev]*len(df['datetime'])
    ),
    row=1,
    col=1
)
fig.append_trace(
    go.Scatter(
        visible=True,
        line=dict(color=shrimp_col, width=2),
        name="",
        x=df['datetime'],
        y=[brine_shrimp_elev]*len(df['datetime'])
    ),
    row=1,
    col=1
)

# Add traces, one for each slider step
for yr in df['year'].unique():
    fig.append_trace(
        go.Scatter(
            visible=False,
            line=dict(color=lake_col, width=2),
            mode="lines",
            name="",
            x=df[df['year'] == yr]['datetime'],
            y=df[df['year'] == yr]['water_elev_ft']
        ),
        row=2,
        col=1
    )

# Make 23rd trace visible (1986)
fig.data[23].visible = True

# Create and add slider
steps = []
for i, yr in enumerate(unique_years):
    step = dict(
        method="update",
        args=[{"visible": [True]*3 + [False]*(num_years)}],  # layout attribute
        label=str(yr)
    )
    step["args"][0]["visible"][i+3] = True  # Toggle i'th trace to "visible"
    steps.append(step)

sliders = [dict(
    active=20,
    currentvalue={"prefix": "Year: "},
    pad={"t": 50},
    steps=steps
)]

fig.update_layout(
    title="Water Elevation of the Great Salt Lake by Time",
    font_family="Optima",
    sliders=sliders,
    height = 800
)


fig.write_html("../../website/plots/plotly_elevation.html")
fig.show()

In [148]:
# Save number of years in which the lake's elevation was recorded
num_years = df['year'].nunique()
unique_years = df['year'].unique()

# Save colors
lake_col = "#265F58"
toxic_col = "#763A4F"
shrimp_col = "#556A82"

# Save elevation levels
brine_shrimp_elev = 4191
lake_bed_elev = 4196.3593632

# Create figure
fig = make_subplots(rows=2, cols=1, subplot_titles=['All Recorded Years', 'By Year'])

# Add plot with full time series
fig.append_trace(
    go.Scatter(
        visible=True,
        line=dict(color=lake_col, width=2),
        name="Water Level",
        x=df['datetime'],
        y=df['water_elev_ft']
    ),
    row=1,
    col=1
)

# Add lines to indicate dried lakebed level and healthy brine shrimp level
fig.append_trace(
    go.Scatter(
        visible=True,
        line=dict(color=toxic_col, width=2),
        name="Toxic Lakebed",
        x=df['datetime'],
        y=[lake_bed_elev]*len(df['datetime'])
    ),
    row=1,
    col=1
)
fig.append_trace(
    go.Scatter(
        visible=True,
        line=dict(color=shrimp_col, width=2),
        name="Healthy Brine Shrimp Elevation",
        x=df['datetime'],
        y=[brine_shrimp_elev]*len(df['datetime'])
    ),
    row=1,
    col=1
)

# Add traces, three for each slider step
for yr in df['year'].unique():
    # Lake elevation
    fig.append_trace(
        go.Scatter(
            visible=False,
            line=dict(color=lake_col, width=2),
            mode="lines",
            showlegend=False,
            name="",
            x=df[df['year'] == yr]['datetime'],
            y=df[df['year'] == yr]['water_elev_ft']
        ),
        row=2,
        col=1
    )

    # Lake bed elevation
    fig.append_trace(
        go.Scatter(
            visible=False,
            line=dict(color=toxic_col, width=2),
            mode="lines",
            showlegend=False,
            name="",
            x=df[df['year'] == yr]['datetime'],
            y=[lake_bed_elev]*len(df[df['year'] == yr]['datetime'])
        ),
        row=2,
        col=1
    )

    # Healthy brine shrimp elevation
    fig.append_trace(
        go.Scatter(
            visible=False,
            line=dict(color=shrimp_col, width=2),
            mode="lines",
            showlegend=False,
            name="",
            x=df[df['year'] == yr]['datetime'],
            y=[brine_shrimp_elev]*len(df[df['year'] == yr]['datetime'])
        ),
        row=2,
        col=1
    )


# Make 1986 traces visible
fig.data[63].visible = True
fig.data[64].visible = True
fig.data[65].visible = True

# Create and add slider
steps = []

# Cycle through all the indices of unique years
for i, yr in enumerate(unique_years):
    # Define the visibility array for each step
    # This code may be confusing at first glance. `visibility_array` is initialized with True as the
    # first three elements (indicating to Plotly to show the first three traces of the figure, which
    # compose the top subplot), with the remaining elements set to False. We add three times the number
    # of years because each step (indicating a year) will have three visible traces on the bottom 
    # subplot.
    # 
    # `step_start_i` specifies where in the visibility array the first trace of the given year is 
    # represented. The index after that would represent the trace of the lake bed elevation, and 
    # `step_end_i` indicates the index of the visibility array that represents the healthy brine
    # shrimp elevation. For each step, i+1 transforms i to the ith element (0->1, etc), and then
    # that is multiplied by three to account for each step having three traces. All the indices in
    # that range are then set to True in the fourth line of code.
    visibility_array = [True]*3 + [False]*(num_years*3)
    step_start_i = ((i+1)*3)
    step_end_i = ((i+1)*3+3)
    visibility_array[step_start_i:step_end_i] = [True]*3

    # Define the step
    step = dict(
        method="update",
        args=[{"visible": visibility_array}],  # layout attribute
        label=str(yr)
    )
    steps.append(step)



# Cycle through all unique years
# for i, yr in enumerate(unique_years):
#     step = dict(
#         method="update",
#         args=[{"visible": [True]*3 + [False]*(num_years)}],  # layout attribute
#         label=str(yr)
#     )
#     step["args"][0]["visible"][i+3] = True  # Toggle i'th trace to "visible"
#     steps.append(step)

sliders = [dict(
    active=20,
    currentvalue={"prefix": "Year: "},
    pad={"t": 50},
    steps=steps
)]

fig.update_layout(
    title="Water Elevation of the Great Salt Lake by Time",
    font_family="Optima",
    xaxis2_title="Date",
    yaxis_title="Elevation of Water (ft)",
    yaxis2_title="Elevation of Water (ft)",
    font=dict(size=14),
    legend = dict(
        orientation="h",
        yanchor="bottom",
        y=0.45,
        xanchor="center",
        x=0.5
    ),
    sliders=sliders,
    height = 800
)


fig.write_html("../../website/plots/plotly_elevation.html")
fig.show()